<a href="https://colab.research.google.com/github/adityav1810/ExploringPytorch/blob/main/UnderstandingPosEmbeddings.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [63]:
import copy

In [64]:
try:
    import google.colab
    IN_COLAB = True
    !pip install einops
    !pip install git+https://github.com/neelnanda-io/Easy-Transformer@no-position-experiment
except:
    IN_COLAB = False

from easy_transformer import EasyTransformer, EasyTransformerConfig
import torch
import numpy as np
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "colab"
import tqdm.auto as tqdm
import einops
from easy_transformer.utils import to_numpy

  Cloning https://github.com/neelnanda-io/Easy-Transformer (to revision no-position-experiment) to /tmp/pip-req-build-nn729sa2
  Running command git clone --filter=blob:none --quiet https://github.com/neelnanda-io/Easy-Transformer /tmp/pip-req-build-nn729sa2
  Running command git checkout -b no-position-experiment --track origin/no-position-experiment
  Switched to a new branch 'no-position-experiment'
  Branch 'no-position-experiment' set up to track remote branch 'no-position-experiment' from 'origin'.
  Resolved https://github.com/neelnanda-io/Easy-Transformer to commit 2b91e7ec49854f74363e5699ae4f8f99a595e65c
  Preparing metadata (setup.py) ... done


In [65]:
# def line(tensor, line_labels=None, yaxis="", xaxis="", **kwargs):
#     tensor = to_numpy(tensor)
#     labels = {"y":yaxis, "x":xaxis}
#     fig = px.line(tensor, labels=labels, **kwargs)
#     if line_labels:
#         for c, label in enumerate(line_labels):
#             fig.data[c].name = label
#     fig.show()

# def imshow(tensor, yaxis="", xaxis="", **kwargs):
#     tensor = to_numpy(tensor)
#     plot_kwargs = {"color_continuous_scale":"RdBu", "color_continuous_midpoint":0.0, "labels":{"x":xaxis, "y":yaxis}}
#     plot_kwargs.update(kwargs)
#     px.imshow(tensor, **plot_kwargs).show()

Model Training

Setup

Defining transformer

In [66]:
cfg = EasyTransformerConfig(
    n_layers = 2,
    d_model=64,
    d_head=64,
    n_heads=1,
    d_mlp=256,
    d_vocab=300,
    n_ctx=50,
    act_fn='relu',
    normalization_type="LN",
)
model = EasyTransformer(cfg)

Moving model to device:  cuda


In [67]:

def deactivate_position(model):
    # Set data to 0
    model.pos_embed.W_pos.data[:] = 0.
    # Stop gradient updates
    model.pos_embed.W_pos.requires_grad = False
deactivate_position(model)



In [68]:
print(model)

EasyTransformer(
  (embed): Embed()
  (hook_embed): HookPoint()
  (pos_embed): PosEmbed()
  (hook_pos_embed): HookPoint()
  (blocks): ModuleList(
    (0-1): 2 x TransformerBlock(
      (ln1): LayerNorm(
        (hook_scale): HookPoint()
        (hook_normalized): HookPoint()
      )
      (ln2): LayerNorm(
        (hook_scale): HookPoint()
        (hook_normalized): HookPoint()
      )
      (attn): Attention(
        (hook_k): HookPoint()
        (hook_q): HookPoint()
        (hook_v): HookPoint()
        (hook_z): HookPoint()
        (hook_attn_scores): HookPoint()
        (hook_attn): HookPoint()
        (hook_result): HookPoint()
      )
      (mlp): MLP(
        (hook_pre): HookPoint()
        (hook_post): HookPoint()
      )
      (hook_attn_out): HookPoint()
      (hook_mlp_out): HookPoint()
      (hook_resid_pre): HookPoint()
      (hook_resid_mid): HookPoint()
      (hook_resid_post): HookPoint()
    )
  )
  (ln_final): LayerNorm(
    (hook_scale): HookPoint()
    (hook_normal

In [69]:
# Test deactivate pos embedding function
# define optim
optim = torch.optim.SGD(model.parameters(),lr = 100.)
print(model.embed.W_E)
print(model.pos_embed.W_pos)
# run for epochs

for i in range(100):
  # dummy data
  token = torch.tensor([[1,2,3,4]]).cuda()
  loss = model(token).sum()
  # update
  loss.backward()
  optim.step()
  optim.zero_grad()
# test output
print(model.embed.W_E)
print(model.pos_embed.W_pos)


Parameter containing:
tensor([[ 0.1927,  0.1487,  0.0901,  ...,  0.1845, -0.1185,  0.1384],
        [ 0.1445,  0.0856,  0.2218,  ...,  0.0340,  0.0720,  0.0411],
        [ 0.1931,  0.1012, -0.1436,  ..., -0.0556,  0.0704,  0.0710],
        ...,
        [ 0.0340, -0.0575,  0.1507,  ...,  0.1330, -0.1922, -0.1609],
        [ 0.0316,  0.0981, -0.0726,  ...,  0.0588,  0.0884, -0.0568],
        [-0.0006,  0.0530,  0.0331,  ..., -0.0178,  0.0054, -0.0561]],
       device='cuda:0', requires_grad=True)
Parameter containing:
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], device='cuda:0')
Parameter containing:
tensor([[ 0.1927,  0.1487,  0.0901,  ...,  0.1845, -0.1185,  0.1384],
        [    nan,     nan,     nan,  ...,     nan,     nan,     nan],
        [    nan,     nan,     nan,  ...,    

Define data and loss function

In [70]:
def make_data_generator(cfg, batch_size, seed=123, incl_bos_token=True):
    torch.manual_seed(seed)
    while True:
        x = torch.randint(1, cfg.d_vocab, (batch_size, cfg.n_ctx))
        if incl_bos_token:
            x[:, 0] = 0
        yield x
data_generator = make_data_generator(cfg, 2)
print(next(data_generator))


tensor([[  0,  93,  34, 155, 274, 116, 114, 248,  68,   3, 298,  83, 194,  20,
           8, 133,  32,  66,  62,  73, 210, 273,  46, 243, 104, 232, 161, 125,
         123, 251,   7,   4, 115, 127,  21,   1,  89, 142,   6,  15, 298, 251,
          88, 229, 108, 114,  23,  88,   3, 265],
        [  0, 118,  46, 274, 105, 268, 131,  35,  19,  58, 226, 278,  27,  25,
         276, 180, 164,   4,  95,  27,  74, 201, 105,  65,  80, 185,  44, 258,
         105,  60,  58,  47, 126,  60, 294, 253, 258, 136,  29, 101, 258,  77,
          80, 180, 159, 169, 122, 117,  27, 194]])


In [71]:
def loss_fn(logits, tokens, return_per_token=False):
    # logit shape: [batch, pos, vocab]
    # token shape: [batch, pos]
    logits = logits[:, 1:]
    tokens = tokens[:, :-1]
    log_probs = logits.log_softmax(-1)
    correct_log_probs = log_probs.gather(-1, tokens[..., None])[..., 0]
    if return_per_token:
        return -correct_log_probs
    else:
        return -correct_log_probs.mean()

# def loss_fn (logits, tokens, return_per_token = False):
#   # get all logits except for the one before
#   logits = logits[:,1:]
#   # get all tokens except for the last
#   tokens = tokens[:,:-1]
#   # convert to softmax
#   log_probs = logits.log_softmax(-1)
#   # get gt
#   correct_log_probs = log_probs.gather(-1,tokens[...,None])[...,0]
#   # for checking individual responses
#   if return_per_token:
#     return -correct_log_probs
#   else:
#     return -correct_log_probs.mean()


In [72]:
# test loss_fn
# Test the loss function works
test_tokens = torch.arange(5)[None, :]
test_logits = torch.randn(1, 5, 10)
test_logits[:, 1, 0]=10.
test_logits[:, 2, 1]=10.
test_logits[:, 3, 2]=10.
test_logits[:, 4, 3]=10.



In [73]:
test_tokens,test_logits


(tensor([[0, 1, 2, 3, 4]]),
 tensor([[[-3.1861e-02, -4.7896e-01,  7.6681e-01,  2.7468e-02,  4.7470e-02,
           -9.2387e-01, -1.0607e+00, -2.3244e+00, -2.0628e+00,  6.3745e-03],
          [ 1.0000e+01,  7.0161e-01, -9.8224e-01,  2.7703e-01,  6.4550e-01,
           -8.9568e-01,  4.9275e-01, -1.4078e-02, -2.7466e-01, -7.6409e-01],
          [-5.8716e-01,  1.0000e+01, -1.2096e+00, -5.5601e-01, -7.7105e-02,
            1.2774e+00, -1.4596e+00, -2.1595e+00, -7.0671e-01, -9.2224e-01],
          [ 3.8954e+00, -6.0270e-01,  1.0000e+01, -2.8774e-01,  5.8206e-01,
            2.0532e-01, -9.8437e-01,  1.9184e+00,  9.4742e-01,  1.6834e+00],
          [ 5.6634e-01,  1.0306e+00,  2.1187e-01,  1.0000e+01, -7.5571e-01,
           -1.9830e-01,  1.2118e+00, -1.2076e+00, -3.0162e-01, -7.0744e-01]]]))

In [74]:
print(loss_fn(test_logits, test_tokens, return_per_token = True))
print(loss_fn(test_logits, test_tokens, return_per_token = False))

tensor([[0.0004, 0.0003, 0.0031, 0.0005]])
tensor(0.0011)


Setup the Optimizer

In [75]:
batch_size = 256
num_epochs = 4000
lr = 1e-4
betas = (0.9, 0.95)
max_grad_norm = 1.0
wd = 0.1
optimizer = torch.optim.AdamW(model.parameters(), lr=lr, betas=betas, weight_decay=wd)
scheduler = torch.optim.lr_scheduler.LambdaLR(optimizer, lambda i: min(i/100, 1.))

data_loader = make_data_generator(cfg, batch_size)

Model Training


load model with no pos embedding

In [76]:
model = EasyTransformer(cfg)
model.load_state_dict(torch.load('/content/no_pos_experiment_state_dict_v0.pth'))
deactivate_position(model)

Moving model to device:  cuda


In [77]:
# losses = []
# for epoch in tqdm.tqdm(range(100)):
#     tokens = next(data_loader)
#     tokens = tokens.cuda()
#     logits = model(tokens)
#     loss = loss_fn(logits, tokens)
#     loss.backward()
#     if max_grad_norm is not None:
#         torch.nn.utils.clip_grad_norm_(model.parameters(), max_grad_norm)
#     optimizer.step()
#     optimizer.zero_grad()
#     scheduler.step()
#     losses.append(loss.item())
#     if epoch % 100 == 0:
#         print(f'Epoch {epoch}: {loss.item()}')


load

In [78]:
model_pos= EasyTransformer(cfg)
model_pos.load_state_dict(torch.load('/content/pos_experiment_state_dict_v0.pth'))

# losses = []
# for epoch in tqdm.tqdm(range(100)):
#     tokens = next(data_loader)
#     tokens = tokens.cuda()
#     logits = model_pos(tokens)
#     loss = loss_fn(logits, tokens)
#     loss.backward()
#     if max_grad_norm is not None:
#         torch.nn.utils.clip_grad_norm_(model_pos.parameters(), max_grad_norm)
#     optimizer.step()
#     optimizer.zero_grad()
#     scheduler.step()
#     losses.append(loss.item())
#     if epoch % 100 == 0:
#         print(f'Epoch {epoch}: {loss.item()}')

Moving model to device:  cuda


<All keys matched successfully>

Interpretting the model

In [79]:
model.pos_embed.W_pos.norm(),model_pos.pos_embed.W_pos.norm()

(tensor(0., device='cuda:0'),
 tensor(5.1113, device='cuda:0', grad_fn=<LinalgVectorNormBackward0>))

Looking at Attention Patterns


In [80]:
big_data_loader = make_data_generator(cfg, 1000)
big_tokens = next(big_data_loader)
big_tokens = big_tokens.cuda()
logits,cache = model.run_with_cache(big_tokens)
logits_p,cache_p = model_pos.run_with_cache(big_tokens)
print("Loss without pos embedding:",loss_fn(logits,big_tokens).item())
print("Loss with pos embedding:",loss_fn(logits_p,big_tokens).item())

Loss without pos embedding: 0.0037237266078591347
Loss with pos embedding: 1.6317072493166052e-07


Attention Pattern with no Positional Embedding

In [81]:
batch_index = 0
tokens = big_tokens[batch_index]
imshow(to_numpy(cache["attn", 0].mean([0, 1])), title="Layer 0 Attention Pattern", height=500, width=500)
imshow(to_numpy(cache["attn", 1].mean([0, 1])), title="Layer 1 Attention Pattern", height=500, width=500)

Attention Pattern with Positional Embedding

In [82]:
imshow(to_numpy(cache_p["attn", 0].mean([0, 1])), title="Layer 0 Attention Pattern", height=500, width=500)
imshow(to_numpy(cache_p["attn", 1].mean([0, 1])), title="Layer 1 Attention Pattern", height=500, width=500)

In [83]:
labels = ["embed","A0","M0","A1","M2"]
def get_residual_stack(c):
  residual_components = [c["embed"], c["attn_out", 0], c["mlp_out", 0], c["attn_out", 1], c["mlp_out", 1]]
  residual_stack = torch.stack(residual_components,0)
  residual_stack = residual_stack - residual_stack.mean(-1, keepdim=True)
  print(residual_stack.shape)
  return residual_stack

In [84]:
res_stack = get_residual_stack(cache)
res_stack_p = get_residual_stack(cache_p)

torch.Size([5, 1000, 50, 64])
torch.Size([5, 1000, 50, 64])


In [85]:
fold_W_U = model.ln_final.w[:, None] * model.unembed.W_U
logit_components = res_stack[:, batch_index] @ fold_W_U/cache["scale", None, "ln_final"][batch_index]
logit_components = logit_components - logit_components.mean(-1, keepdim=True)
line(logit_components[:, torch.arange(1, model.cfg.n_ctx).cuda(), tokens[:-1]].T, line_labels=labels)

In [86]:
fold_W_U_p = model_pos.ln_final.w[:, None] * model_pos.unembed.W_U
logit_components = res_stack_p[:, batch_index] @ fold_W_U_p/cache_p["scale", None, "ln_final"][batch_index]
logit_components = logit_components - logit_components.mean(-1, keepdim=True)
line(logit_components[:, torch.arange(1, model_pos.cfg.n_ctx).cuda(), tokens[:-1]].T, line_labels=labels)

Folding LayerNorm

In [87]:
analysis_cfg = EasyTransformerConfig(
    n_layers = 2,
    d_model=64,
    d_head=64,
    n_heads=1,
    d_mlp=256,
    d_vocab=300,
    n_ctx=50,
    act_fn='relu',
    normalization_type="LNPre",
    init_weights=False,
)
analysis_model = EasyTransformer(analysis_cfg)
state_dict = model.state_dict()
analysis_model.load_and_process_state_dict(state_dict, fold_ln=True, center_writing_weights=True, center_unembed=True)
deactivate_position(analysis_model)

Moving model to device:  cuda


In [88]:
print(loss_fn(analysis_model(big_tokens),big_tokens))
print(loss_fn(model(big_tokens),big_tokens))

tensor(0.0037, device='cuda:0', grad_fn=<NegBackward0>)
tensor(0.0037, device='cuda:0', grad_fn=<NegBackward0>)


In [89]:
old_model = copy.deepcopy(model)
model = analysis_model

Understand Attn0


In [96]:
QK = model.W_E @ model.W_Q[0, 0] @ model.W_K[0, 0].T @ model.W_E.T
imshow(QK, yaxis="Query", xaxis="Key")

In [91]:
QK_p = model_pos.W_E @ model_pos.W_Q[0, 0] @ model_pos.W_K[0, 0].T @ model_pos.W_E.T
imshow(QK_p, yaxis="Query", xaxis="Key")

In [97]:
OV = model.W_E @ model.W_V[0, 0] @ model.W_O[0, 0] @ model.W_in[0]
imshow(OV, yaxis="Input Vocab", xaxis="Neuron")

In [99]:
OV_p = model_pos.W_E @ model_pos.W_V[0, 0] @ model_pos.W_O[0, 0] @ model_pos.W_in[0]
imshow(OV_p, yaxis="Input Vocab", xaxis="Neuron")

In [100]:
line(OV[:, torch.randint(0, 256, (5,))])

In [101]:
line(OV_p[:, torch.randint(0, 256, (5,))])